In [123]:
import math
from neuroml import NeuroMLDocument
from neuroml import Cell
from neuroml import BiophysicalProperties
from neuroml import MembraneProperties
from neuroml import IncludeType, Include, Property
from neuroml import ChannelDensity, ChannelDensityNonUniform, ChannelDensityNernst, ChannelDensityGHK2, ChannelDensityVShift
from neuroml import SpikeThresh
from neuroml import SpecificCapacitance
from neuroml import InitMembPotential
from neuroml import IntracellularProperties, Species
from neuroml import Resistivity
from neuroml import Morphology, Segment, Point3DWithDiam, SegmentGroup
from neuroml import Network, Population, InhomogeneousParameter, ProximalDetails
from neuroml import PulseGenerator, ExplicitInput
from neuroml import InhomogeneousParameter, InhomogeneousValue, VariableParameter
from pyneuroml import pynml
import numpy as np
from pyneuroml.lems import LEMSSimulation
from CellBuilder import (create_cell, add_segment, add_channel_density, set_init_memb_potential, set_resistivity, set_specific_capacitance, get_seg_group_by_id)
import typing
import plotly.graph_objects as go
import logging

logger = logging.getLogger(__name__)
logger.setLevel(logging.DEBUG)

In [79]:
def generate_interactive_plot(
    xvalues: typing.List[float],
    yvalues: typing.List[float],
    title: str,
    labels: typing.Optional[typing.List[str]] = None,
    linestyles: typing.Optional[typing.List[str]] = None,
    linewidths: typing.Optional[
        typing.Union[typing.List[int], typing.List[float]]
    ] = None,
    markers: typing.Optional[typing.Union[typing.List[str], typing.List[int]]] = None,
    markersizes: typing.Optional[
        typing.Union[typing.List[float], typing.List[int]]
    ] = None,
    plot_bgcolor: typing.Optional[str] = None,
    modes: typing.Optional[typing.List[str]] = None,
    xaxis: str = None,
    yaxis: str = None,
    legend_title: str = None,
    xaxis_color: str = "#fff",
    yaxis_color: str = "#fff",
    xaxis_width: typing.Union[float, int] = 1,
    yaxis_width: typing.Union[float, int] = 1,
    xaxis_mirror: typing.Union[str, bool] = False,
    yaxis_mirror: typing.Union[str, bool] = False,
    xaxis_spikelines: bool = False,
    yaxis_spikelines: bool = False,
    grid: bool = True,
    logx: bool = False,
    logy: bool = False,
    layout: typing.Optional[dict] = None,
    show_interactive: bool = True,
    save_figure_to: typing.Optional[str] = None,
) -> None:
    """Utility function to generate interactive plots using Plotly.
    This function can be used to generate graphs with multiple plot lines.
    For example, to plot two metrics you can use:
    ::
        generate_interactive_plot(xvalues=[[ax1, ax2, ax3], [bx1, bx2, bx3]], yvalues=[[ay1, ay2, ay3], [by1, by2, by3]], labels=["metric 1", "metric 2"])
    Please note that while plotting multiple plots, you should take care to
    ensure that the number of x values and y values for each metric correspond.
    These lists are passed directly to Plotly for plotting without additional
    sanity checks.
    A number of options are provided for convenience to allow plotting of
    multiple traces in the same plot and modification of common layout options.
    A layout dict can also be passed instead, which will overwrite any
    individually set options. If you need more customisation, please look at
    the source code of this method to write your own.
    See the plotly documentation for more information:
    https://plotly.com/python-api-reference/generated/plotly.graph_objects.scatter.html
    :param xvalues: X values
    :type xvalues: list of lists
    :param yvalues: Y values
    :type yvalues: lists of lists
    :param title: title of plot
    :type title: str
    :param labels: labels for each plot (default: None)
    :type labels: list of strings
    :param modes: modes of individual plots: "markers", "lines",
        "lines+markers": default "lines+markers"
    :type modes: str
    :param linestyles: list of line styles (default: None)
    :type linestyles: list strings
    :param linewidths: list of line widths (default: None)
    :type linewidths: list of floats/int
    :param markers: list of markers (default: None)
    :type markers: list of plotly marker values. See:
        https://plotly.com/python-api-reference/generated/plotly.graph_objects.scatter.html#plotly.graph_objects.scatter.Marker.symbol
    :param markersizes: list of marker sizes (default: None)
    :type markersizes: list of ints/floats
    :param plot_bgcolor: background color of plotting area b/w axes
        See https://plotly.com/python-api-reference/generated/plotly.graph_objects.Figure.html#plotly.graph_objects.Figure
    :type plot_bgcolor: str
    :param xaxis: label of X axis (default: None)
    :type xaxis: str
    :param yaxis: label of Y axis (default: None)
    :type yaxis: str
    :param legend_title: title of legend
    :type legend_title: str
    :param xaxis_color: color of xaxis
    :type xaxis_color: str
    :param yaxis_color: color of yaxis
    :type yaxis_color: str
    :param xaxis_width: width of xaxis
    :type xaxis_width: int/float
    :param yaxis_width: width of yaxis
    :type yaxis_width: int/float
    :param xaxis_mirror: xaxis mirror options:
        https://plotly.com/python/reference/layout/xaxis/#layout-xaxis-mirror
    :type xaxis_mirror: bool/str
    :param yaxis_mirror: yaxis mirror options
        https://plotly.com/python/reference/layout/xaxis/#layout-xaxis-mirror
    :type yaxis_mirror: bool/str
    :param xaxis_spikelines: toggle spike lines on x axis
        https://plotly.com/python/hover-text-and-formatting/#spike-lines
    :type xaxis_spikelines: bool/str
    :param yaxis_spikelines: toggle spike lines on x axis
        https://plotly.com/python/hover-text-and-formatting/#spike-lines
    :type yaxis_spikelines: bool/str
    :param grid: enable/disable grid (default: True)
    :type grid: boolean
    :param logx: should the x axis be in log scale (default: False)
    :type logx: boolean
    :param logy: should the y ayis be in log scale (default: False)
    :type logy: boolean
    :param layout: plot layout properties: these will overwrite all other
        layout options specified
        See:
        https://plotly.com/python-api-reference/generated/plotly.graph_objects.Figure.html#plotly.graph_objects.Figure.update_layout
    :type layout: dict
    :param show_interactive: toggle whether interactive plot should be opened (default: True)
    :type show_interactive: bool
    :param save_figure_to: location to save generated figure to (default: None)
        Requires the kaleido package to be installed.
        See for supported formats:
        https://plotly.com/python-api-reference/generated/plotly.graph_objects.Figure.html#plotly.graph_objects.Figure.write_image
        Note: you can also save the file from the interactive web page.
    :type save_figure_to: str
    """
    fig = go.Figure()

    if len(xvalues) != len(yvalues):
        raise ValueError("length of x values does not match length of y values")

    if not labels or len(labels) != len(xvalues):
        raise ValueError("labels not provided correctly")

    if not markersizes:
        markersizes = len(xvalues) * [6.0]
    if not markers:
        markers = len(xvalues) * [0]
    if not linestyles:
        linestyles = len(xvalues) * ["solid"]
    if not linewidths:
        linewidths = len(xvalues) * [2.0]
    if not modes:
        modes = len(xvalues) * ["lines+markers"]

    for i in range(len(xvalues)):
        fig.add_trace(
            go.Scatter(
                x=xvalues[i],
                y=yvalues[i],
                name=labels[i],
                marker={"size": markersizes[i], "symbol": markers[i]},
                line={"dash": linestyles[i], "width": linewidths[i]},
                mode=modes[i],
            ),
        )

    fig.update_layout(
        title={"text": title, "xanchor": "auto"},
        xaxis_title=xaxis,
        yaxis_title=yaxis,
        legend_title=legend_title,
        plot_bgcolor=plot_bgcolor,
        hovermode="closest",
    )

    if logx:
        fig.update_xaxes(type="log")
    else:
        fig.update_xaxes(type="linear")
    if logy:
        fig.update_yaxes(type="log")
    else:
        fig.update_yaxes(type="linear")
    fig.update_xaxes(
        showgrid=grid,
        linecolor=xaxis_color,
        linewidth=xaxis_width,
        mirror=xaxis_mirror,
        showspikes=xaxis_spikelines,
    )
    fig.update_yaxes(
        showgrid=grid,
        linecolor=yaxis_color,
        linewidth=yaxis_width,
        mirror=yaxis_mirror,
        showspikes=yaxis_spikelines,
    )

    if layout:
        fig.update_layout(layout, overwrite=True)

    if show_interactive:
        fig.show()

    if save_figure_to:
        logger.info(
            "Saving image to %s of plot: %s" % (os.path.abspath(save_figure_to), title)
        )
        fig.write_image(save_figure_to, scale=2, width=1024, height=768)
        logger.info("Saved image to %s of plot: %s" % (save_figure_to, title))

In [97]:
def main():
    """Main function

    Include the NeuroML model into a LEMS simulation file, run it, plot some
    data.
    """
    # Simulation bits

    sim_id = "pyr_multi_comp"
    simulation = LEMSSimulation(sim_id=sim_id, duration=700, dt=0.005, simulation_seed=123)

    # Include the NeuroML model file
    simulation.include_neuroml2_file(create_pyr_network())
    # Assign target for the simulation
    simulation.assign_simulation_target("single_pyr_cell_network")

    # Recording information from the simulation
    simulation.create_output_file(id="output0", file_name=sim_id + ".dat")
    simulation.add_column_to_output_file("output0", column_id="pop0[0]_v", quantity="pop0[0]/v")

    # Recording information from the simulation
    # simulation.create_output_file(id="na_m", file_name=sim_id + ".na_m.dat")
    # simulation.add_column_to_output_file("na_m", column_id="pop0[0]_na_m", quantity="pop0[0]/pyr_b_prop/membraneProperties/nat_channels/nat/m/q")

    # simulation.create_output_file(id="na_h", file_name=sim_id + ".na_h.dat")
    # simulation.add_column_to_output_file("na_h", column_id="pop0[0]_na_h", quantity="pop0[0]/pyr_b_prop/membraneProperties/nat_channels/nat/h/q")

    # simulation.create_output_file(id="kfast_n", file_name=sim_id + ".kfast_n.dat")
    # simulation.add_column_to_output_file("kfast_n", column_id="pop0[0]_kfast_n", quantity="pop0[0]/pyr_b_prop/membraneProperties/kfast_channels/kfast/n/q")

    # simulation.create_output_file(id="nap_m", file_name=sim_id + ".nap_m.dat")
    # simulation.add_column_to_output_file("nap_m", column_id="pop0[0]_nap_m", quantity="pop0[0]/pyr_b_prop/membraneProperties/nap_channels/nap/m/q")

    # simulation.create_output_file(id="kslow_a", file_name=sim_id + ".kslow_a.dat")
    # simulation.add_column_to_output_file("kslow_a", column_id="pop0[0]_kslow_a", quantity="pop0[0]/pyr_b_prop/membraneProperties/kslow_channels/kslow/a/q")

    # simulation.create_output_file(id="kslow_b", file_name=sim_id + ".kslow_b.dat")
    # simulation.add_column_to_output_file("kslow_b", column_id="pop0[0]_kslow_b", quantity="pop0[0]/pyr_b_prop/membraneProperties/kslow_channels/kslow/b/q")

    # simulation.create_output_file(id="ikm_m", file_name=sim_id + ".ikm_m.dat")
    # simulation.add_column_to_output_file("ikm_m", column_id="pop0[0]_ikm_m", quantity="pop0[0]/pyr_b_prop/membraneProperties/km_channels/km/m/q")

    # Save LEMS simulation to file
    sim_file = simulation.save_to_file()

    # Run the simulation using the default jNeuroML simulator
    # pynml.run_lems_with_jneuroml(sim_file, max_memory="2G", nogui=True, plot=False)
    # Plot the data
    # plot_data(sim_id)

In [80]:
def plot_data(sim_id):
    """Plot the sim data.

    Load the data from the file and plot the graph for the membrane potential
    using the pynml generate_plot utility function.

    :sim_id: ID of simulaton

    """
    data_array = np.loadtxt(sim_id + ".dat")
    # pynml.generate_plot([data_array[:, 0]], [data_array[:, 1]], "Membrane potential", show_plot_already=False, save_figure_to=sim_id + "-v.png", xaxis="time (s)", yaxis="membrane potential (V)")
    generate_interactive_plot(xvalues=[data_array[:, 0]],
                        yvalues=[data_array[:, 1]],
                        labels=["Vm"],
                        title="Membrane Potential plot",
                        show_interactive=True, xaxis="time (s)", yaxis="Vm")
                        
    # data_array_na_m = np.loadtxt(sim_id + ".na_m.dat")
    # pynml.generate_plot([data_array_na_m[:, 0]], [data_array_na_m[:, 1]], "Nat m gate", show_plot_already=False, save_figure_to=sim_id + "-na_m.png", xaxis="time (s)", yaxis="q")

    # data_array_na_h = np.loadtxt(sim_id + ".na_h.dat")
    # pynml.generate_plot([data_array_na_h[:, 0]], [data_array_na_h[:, 1]], "Nat h gate", show_plot_already=False, save_figure_to=sim_id + "-na_h.png", xaxis="time (s)", yaxis="q")

    # data_array_kfast_n = np.loadtxt(sim_id + ".kfast_n.dat")
    # pynml.generate_plot([data_array_kfast_n[:, 0]], [data_array_kfast_n[:, 1]], "Kfast n gate", show_plot_already=False, save_figure_to=sim_id + "-kfast_n.png", xaxis="time (s)", yaxis="q")

    # data_array_nap_m = np.loadtxt(sim_id + ".nap_m.dat")
    # pynml.generate_plot([data_array_nap_m[:, 0]], [data_array_nap_m[:, 1]], "Nap m gate", show_plot_already=False, save_figure_to=sim_id + "-nap_m.png", xaxis="time (s)", yaxis="q")

    # data_array_kslow_a = np.loadtxt(sim_id + ".kslow_a.dat")
    # pynml.generate_plot([data_array_kslow_a[:, 0]], [data_array_kslow_a[:, 1]], "Kslow a gate", show_plot_already=False, save_figure_to=sim_id + "-kslow_a.png", xaxis="time (s)", yaxis="q")

    # data_array_kslow_b = np.loadtxt(sim_id + ".kslow_b.dat")
    # pynml.generate_plot([data_array_kslow_b[:, 0]], [data_array_kslow_b[:, 1]], "Kslow b gate", show_plot_already=False, save_figure_to=sim_id + "-kslow_b.png", xaxis="time (s)", yaxis="q")

    # data_array_ikm_m = np.loadtxt(sim_id + ".ikm_m.dat")
    # pynml.generate_plot([data_array_ikm_m[:, 0]], [data_array_ikm_m[:, 1]], "IKM m gate", show_plot_already=False, save_figure_to=sim_id + "-ikm_m.png", xaxis="time (s)", yaxis="q")

In [128]:
def create_pyr_cell():
    pyr_cell_doc = NeuroMLDocument(id='cell', notes="Layer 5 Pyramidal cell")
    cell = create_cell("pyr")
    nml_cell_file = cell.id + ".cell.nml"

    # pyr_cell_doc.includes.append(IncludeType("kca.channel.nml"))
    # pyr_cell_doc.includes.append(IncludeType("sca.channel.nml"))
    # pyr_cell_doc.includes.append(IncludeType("cad.nml"))

    # pyr_cell_doc.includes.append(IncludeType("kslow.channel.nml"))
    pyr_cell_doc.includes.append(IncludeType("nat.channel.nml"))
    # pyr_cell_doc.includes.append(IncludeType("nap.channel.nml"))
    # pyr_cell_doc.includes.append(IncludeType("IKM.channel.nml"))

    # Add two soma segments
    diam = 23.1453
    # soma_0 = add_segment(cell,
    #                     prox=[0.0, 0.0, 0.0, diam],
    #                     dist=[diam, 0.0, 0.0, diam],
    #                     name="Seg0_soma",
    #                     group="soma")
    soma_0 = add_segment(cell,
                         prox=[0.0, 0.0, 0.0, diam],
                         dist=[11.5726, 0.0, 0.0, diam],
                         name="Seg0_soma",
                         group="soma_0")

    soma_1 = add_segment(cell,
                         prox=None,
                         dist=[diam, 0.0, 0.0, diam],
                         name="Seg1_soma",
                         parent=soma_0,
                         group="soma_0")

    # # Add hillock segments
    # hillock_0 = add_segment(cell,
    #                         parent=soma_0,
    #                         prox=[0, 0, 0, 3.35],
    #                         dist=[-2, 1.74846e-07, 0, 3.35],
    #                         name="Seg0_hillock",
    #                         group="hillock")

    # hillock_1 = add_segment(cell,
    #                         parent=hillock_0,
    #                         prox=None,
    #                         dist=[-6, 5.24537e-07, 0, 3.05],
    #                         name="Seg1_hillock",
    #                         group="hillock")

    # hillock_2 = add_segment(cell,
    #                         parent=hillock_1,
    #                         prox=None,
    #                         dist=[-10, 8.74228e-07, 0, 2.75],
    #                         name="Seg2_hillock",
    #                         group="hillock")

    # hillock_3 = add_segment(cell,
    #                         parent=hillock_2,
    #                         prox=None,
    #                         dist=[-14, 1.22392e-06, 0, 2.45],
    #                         name="Seg3_hillock",
    #                         group="hillock")

    # hillock_4 = add_segment(cell,
    #                         parent=hillock_3,
    #                         prox=None,
    #                         dist=[-18, 1.57361e-06, 0, 2.15],
    #                         name="Seg4_hillock",
    #                         group="hillock"
    #                         )

    # hillock_5 = add_segment(cell,
    #                         parent=hillock_4,
    #                         prox=None,
    #                         dist=[-20, 1.7486e-06, 0, 2.15],
    #                         name="Seg5_hillock",
    #                         group="hillock"
    #                         )

    # Add basal segments
    basal_0 = add_segment(cell,
                          parent=soma_0,
                          prox=[11.5726, 0, 0, 8.74536],
                          dist=[11.5726, 128.5, 0, 8.74536],
                          name="Seg0_basal",
                          group="basal")

    basal_1 = add_segment(cell,
                          parent=basal_0,
                          prox=None,
                          dist=[11.5726, 257, 0, 8.74536],
                          name="Seg1_basal",
                          group="basal") 

    # # Add apical segments
    # apical_0 = add_segment(cell,
    #                        parent=soma_1,
    #                        prox=[23.1453, 0, 0, 5.92845],
    #                        dist=[73.1453, 0, 0, 5.92845],
    #                        name="Seg0_apical",
    #                        group="apical")

    # apical_1 = add_segment(cell,
    #                        parent=apical_0,
    #                        prox=None,
    #                        dist=[173.145, 0, 0, 5.92845],
    #                        name="Seg1_apical",
    #                        group="apical")

    # apical_2 = add_segment(cell,
    #                       parent=apical_1,
    #                       prox=None,
    #                       dist=[273.145, 0, 0, 5.92845],
    #                       name="Seg2_apical",
    #                       group="apical")

    # apical_3 = add_segment(cell,
    #                       parent=apical_2,
    #                       prox=None,
    #                       dist=[373.145, 0, 0, 5.92845],
    #                       name="Seg3_apical",
    #                       group="apical")

    # apical_4 = add_segment(cell,
    #                     parent=apical_3,
    #                     prox=None,
    #                     dist=[473.145, 0, 0, 5.92845],
    #                     name="Seg4_apical",
    #                     group="apical")

    # apical_5 = add_segment(cell,
    #                     parent=apical_4,
    #                     prox=None,
    #                     dist=[523.145, 0, 0, 5.92845],
    #                     name="Seg5_apical",
    #                     group="apical")

    # # Add iseg segments
    # iseg_0 = add_segment(cell,
    #                     parent=hillock_5,
    #                     prox=[-20, 1.74846e-06, 0, 1.95],
    #                     dist=[-22.5, 2.12595e-06, 0, 1.95],
    #                     name="Seg0_iseg",
    #                     group="iseg")

    # iseg_1 = add_segment(cell,
    #                     parent=iseg_0,
    #                     prox=None,
    #                     dist=[-27.5, 2.88092e-06, 0, 1.85],
    #                     name="Seg1_iseg",
    #                     group="iseg")

    # iseg_2 = add_segment(cell,
    #                     parent=iseg_1,
    #                     prox=None,
    #                     dist=[-32.5, 3.6359e-06, 0, 1.75],
    #                     name="Seg2_iseg",
    #                     group="iseg")

    # iseg_3 = add_segment(cell,
    #                     parent=iseg_2,
    #                     prox=None,
    #                     dist=[-37.5, 4.39088e-06, 0, 1.65],
    #                     name="Seg3_iseg",
    #                     group="iseg")

    # iseg_4 = add_segment(cell,
    #                     parent=iseg_3,
    #                     prox=None,
    #                     dist=[-42.5, 5.14586e-06, 0, 1.55],
    #                     name="Seg4_iseg",
    #                     group="iseg")

    # iseg_5 = add_segment(cell,
    #                     parent=iseg_4,
    #                     prox=None,
    #                     dist=[-45, 5.52335e-06, 0, 1.55],
    #                     name="Seg5_iseg",
    #                     group="iseg")

    # # Add tuft segments
    # tuft_0 = add_segment(cell,
    #                     parent=apical_5,
    #                     prox=[523.145, 0, 0, 6.01807],
    #                     dist=[647.895, 0, 0, 6.01807],
    #                     name="Seg0_tuft",
    #                     group="tuft"
    #                     )

    # tuft_1 = add_segment(cell,
    #                     parent=tuft_0,
    #                     prox=None,
    #                     dist=[897.395, 0, 0, 6.01807],
    #                     name="Seg1_tuft",
    #                     group="tuft"
    #                     )

    # tuft_2 = add_segment(cell,
    #                     parent=tuft_1,
    #                     prox=None,
    #                     dist=[1022.15, 0, 0, 6.01807],
    #                     name="Seg2_tuft",
    #                     group="tuft"
    #                     )

    # # Add axon segments
    # axon_0 = add_segment(cell,
    #                     parent=iseg_5,
    #                     prox=[-45, 5.52335e-06, 0, 1.5],
    #                     dist=[-295, 4.32723e-05, 0, 1.5],
    #                     name="Seg0_axon",
    #                     group="axon_0"
    #                     )

    # axon_1 = add_segment(cell,
    #                     parent=axon_0,
    #                     prox=None,
    #                     dist=[-545, 8.10213e-05, 0, 1.5],
    #                     name="Seg1_axon",
    #                     group="axon_0")

    for section_name in ["soma_0", "hillock", "basal", "apical", "iseg", "tuft", "axon_0"]:
        section_group = get_seg_group_by_id(section_name, cell)
        if section_group is None:
            continue
        else:
            section_group.neuro_lex_id = 'sao864921383'
            if section_name in ["apical", "hillock", "iseg"]:
                section_group.properties.append(Property(tag="numberInternalDivisions", value="5"))
            elif section_name in ["tuft"]:
                section_group.properties.append(Property(tag="numberInternalDivisions", value="2"))
            else:
                continue

    soma_seg_group = get_seg_group_by_id("soma_group", cell)
    soma_seg_group.includes.append(Include(segment_groups="soma_0"))
    soma_seg_group.properties.append(Property(tag="color", value="0 0 0.8"))

    basal_seg_group = SegmentGroup(neuro_lex_id=None, id="basal_group")
    basal_seg_group.includes.append(Include(segment_groups="basal"))

    axosomatic = SegmentGroup(neuro_lex_id=None, id="axosomatic_list")
    # apicaltree = SegmentGroup(neuro_lex_id=None, id="apicaltree_list")
    # axon = SegmentGroup(neuro_lex_id=None, id="axon_list")

    cell.morphology.segment_groups.append(axosomatic)
    # cell.morphology.segment_groups.append(apicaltree)
    # cell.morphology.segment_groups.append(axon)
    cell.morphology.segment_groups.append(basal_seg_group)

    axosomatic_group = get_seg_group_by_id("axosomatic_list", cell)
    axosomatic_group.includes.append(Include(segment_groups="soma_0"))
    # axosomatic_group.includes.append(Include(segment_groups="hillock"))
    axosomatic_group.includes.append(Include(segment_groups="basal"))
    # axosomatic_group.includes.append(Include(segment_groups="iseg"))
    # axosomatic_group.includes.append(Include(segment_groups="axon"))
    axosomatic_group.properties.append(Property(tag="color", value="0.8 0 0"))

    # apicaltree_group = get_seg_group_by_id("apicaltree_list", cell)
    # apicaltree_group.includes.append(Include(segment_groups="apical"))
    # apicaltree_group.includes.append(Include(segment_groups="tuft"))

    # axon_group = get_seg_group_by_id("axon_list", cell)
    # axon_group.includes.append(Include(segment_groups="hillock"))
    # axon_group.includes.append(Include(segment_groups="iseg"))
    # axon_group.includes.append(Include(segment_groups="axon"))


    # for g in ['apicaltree_list', 'apical']:
    #     seg_group = get_seg_group_by_id(g, cell)
    #     seg_group.inhomogeneous_parameters.append(
    #         InhomogeneousParameter(
    #             id="PathLengthOver_" + g,
    #             variable="p",
    #             metric="Path Length from root",
    #             proximal=ProximalDetails(
    #                 translation_start="0")))

    # # channels
    # # leak
    add_channel_density(cell, pyr_cell_doc,
                        cd_id="axosomatic_gpas",
                        cond_density="0.485726 S_per_m2",
                        ion_channel="pas",
                        ion_chan_def_file="pas.channel.nml",
                        erev="-80.3987 mV",
                        ion="non_specific",
                        group="axosomatic_list")

    # add_channel_density(cell, pyr_cell_doc,
    #                 cd_id="apicaltree_gpas",
    #                 cond_density="0.381196 S_per_m2",
    #                 ion_channel="pas",
    #                 ion_chan_def_file="pas.channel.nml",
    #                 erev="-80.3987 mV",
    #                 ion="non_specific",
    #                 group="apicaltree_list")                     

    # add_channel_density(cell, pyr_cell_doc,
    #                     cd_id="soma_gpas",
    #                     cond_density="0.485726 S_per_m2",
    #                     ion_channel="pas",
    #                     ion_chan_def_file="pas.channel.nml",
    #                     erev="-80.3987 mV",
    #                     ion="non_specific",
    #                     group="soma_group")
# nat_soma
    # add_channel_density(cell, pyr_cell_doc,
    #                     cd_id="nat_soma",
    #                     cond_density="236.616175 S_per_m2",
    #                     ion_channel="nat",
    #                     ion_chan_def_file="nat.channel.nml",
    #                     erev="55mV",
    #                     ion="na",
    #                     group="soma_group")
    nat_soma_cd = ChannelDensityVShift(id="nat_soma", cond_density="236.616175 S_per_m2", erev="55 mV", v_shift="-10mV", ion="na", ion_channel="nat",
                                        segment_groups="soma_group")
    cell.biophysical_properties.membrane_properties.channel_density_v_shifts.append(nat_soma_cd)


# # nat_hillock
#     add_channel_density(cell, pyr_cell_doc,
#                     cd_id="nat_hillock",
#                     cond_density="9512.289205 S_per_m2",
#                     ion_channel="nat",
#                     ion_chan_def_file="nat.channel.nml",
#                     erev="55mV",
#                     ion="na",
#                     group="hillock")
    
# # nat_iseg
#     add_channel_density(cell, pyr_cell_doc,
#                     cd_id="nat_iseg",
#                     cond_density="13326.766938 S_per_m2",
#                     ion_channel="nat",
#                     ion_chan_def_file="nat.channel.nml",
#                     erev="55mV",
#                     ion="na",
#                     group="iseg")

# # nat_tuft
#     add_channel_density(cell, pyr_cell_doc,
#                     cd_id="nat_tuft",
#                     cond_density="47.82 S_per_m2",
#                     ion_channel="nat",
#                     ion_chan_def_file="nat.channel.nml",
#                     erev="55mV",
#                     ion="na",
#                     group="tuft")

# kfast_soma
    add_channel_density(cell, pyr_cell_doc,
                        cd_id="kfast_soma",
                        cond_density="67.197508 S_per_m2",
                        ion_channel="kfast",
                        ion_chan_def_file="kfast.channel.nml",
                        erev="-80mV",
                        ion="k",
                        group="soma_group")

# kslow_soma
    add_channel_density(cell, pyr_cell_doc,
                        cd_id="kslow_soma",
                        cond_density="475.82 S_per_m2",
                        ion_channel="kslow",
                        ion_chan_def_file="kslow.channel.nml",
                        erev="-80mV",
                        ion="k",
                        group="soma_group")   

# nap_soma
    add_channel_density(cell, pyr_cell_doc,
                        cd_id="nap_soma",
                        cond_density="1.44 S_per_m2",
                        ion_channel="nap",
                        ion_chan_def_file="nap.channel.nml",
                        erev="55mV",
                        ion="na",
                        group="soma_group")  

# km_soma
    add_channel_density(cell, pyr_cell_doc,
                        cd_id="km_soma",
                        cond_density="10.459916 S_per_m2",
                        ion_channel="km",
                        ion_chan_def_file="IKM.channel.nml",
                        erev="-80mV",
                        ion="k",
                        group="soma_group")

# ih_basal
    add_channel_density(cell, pyr_cell_doc,
                        cd_id="ih_basal",
                        cond_density="11.04 S_per_m2",
                        ion_channel="ih",
                        ion_chan_def_file="ih.channel.nml",
                        erev="-47mV",
                        ion="hcn",
                        group="basal_group")

# # sca_tuft
#     sca_tuft = ChannelDensity(id="tuft_sca", ion_channel="sca", cond_density="0.45423528 S_per_m2", segment_groups="tuft", ion="ca", erev="140mV")
#     cell.biophysical_properties.membrane_properties.channel_densities.append(sca_tuft)

# # kca_tuft
#     kca_tuft = ChannelDensity(id="tuft_kca", ion_channel="kca", cond_density="6.15058501 S_per_m2", segment_groups="tuft", ion="k", erev="-80mV")
#     cell.biophysical_properties.membrane_properties.channel_densities.append(kca_tuft)

# # Calculating the kfast conduction density using variable parameter for segment group apicaltree                           
#     gbar_kfast_apicaltree = VariableParameter(parameter="condDensity",
#                                             segment_groups="apicaltree_list",
#                                             inhomogeneous_value=InhomogeneousValue(inhomogeneous_parameters="PathLengthOver_apicaltree_list",
#                                             value="67.197508*exp(-p/20.075497)"))
#     kfast_apicaltree_list = ChannelDensityNonUniform(id="apicaltree_g_kfast", ion_channel="kfast", erev="-80 mV", ion="k")
#     kfast_apicaltree_list.variable_parameters.append(gbar_kfast_apicaltree)

# # Calculating the kfast conduction density using variable parameter for segment group apicaltree
#     gbar_kslow_apicaltree = VariableParameter(parameter="condDensity",
#                                             segment_groups="apicaltree_list",
#                                             inhomogeneous_value=InhomogeneousValue(inhomogeneous_parameters="PathLengthOver_apicaltree_list",
#                                             value="475.820646*exp(-p/37.711817)"))
#     kslow_apicaltree_list = ChannelDensityNonUniform(id="apicaltree_g_kslow", ion_channel="kslow", erev="-80mV", ion="k")
#     kslow_apicaltree_list.variable_parameters.append(gbar_kslow_apicaltree)

# # Calculating the nat conduction density using variable parameter for segment group apical
#     gbar_nat_apical = VariableParameter(parameter="condDensity",
#                                         segment_groups="apical",
#                                         inhomogeneous_value=InhomogeneousValue(inhomogeneous_parameters="PathLengthOver_apical",
#                                         value="47.34461*p+236.616175"))
#     nat_apical = ChannelDensityNonUniform(id="apical_g_nat", ion_channel="nat", erev="55 mV", ion="na")
#     nat_apical.variable_parameters.append(gbar_nat_apical)

# # Calculating the nat conduction density using variable parameter for segment group apical
#     gbar_ih_apical = VariableParameter(parameter="condDensity",
#                                         segment_groups="apical",
#                                         inhomogeneous_value=InhomogeneousValue(inhomogeneous_parameters="PathLengthOver_apical",
#                                         value="0.0323896*p"))
#     ih_apical = ChannelDensityNonUniform(id="apical_g_ih", ion_channel="ih", erev="-47 mV", ion="hcn")
#     ih_apical.variable_parameters.append(gbar_ih_apical)

#     cell.biophysical_properties.membrane_properties.channel_density_non_uniforms.append(kfast_apicaltree_list)
#     cell.biophysical_properties.membrane_properties.channel_density_non_uniforms.append(kslow_apicaltree_list)
#     cell.biophysical_properties.membrane_properties.channel_density_non_uniforms.append(nat_apical)
#     cell.biophysical_properties.membrane_properties.channel_density_non_uniforms.append(ih_apical)

    # Other cell properties
    set_specific_capacitance(cell, "2.23041 uF_per_cm2", group="axosomatic_list")
    # set_specific_capacitance(cell, "1.750419 uF_per_cm2", group="apicaltree_list")
    cell.biophysical_properties.membrane_properties.spike_threshes.append(SpikeThresh(value="-20mV"))
    # set_specific_capacitance(cell, "2.23041 uF_per_cm2", group="soma_group")
    set_init_memb_potential(cell, "-67mV")
    # set_resistivity(cell, "0.082 kohm_cm")
    set_resistivity(cell, "0.082 kohm_cm", "soma_group")
    # set_resistivity(cell, "0.082 kohm_cm", "hillock")
    # set_resistivity(cell, "0.082 kohm_cm", "iseg")
    # set_resistivity(cell, "0.082 kohm_cm", "axon")
    set_resistivity(cell, "0.734 kohm_cm", "basal_group")
    # set_resistivity(cell, "0.527 kohm_cm", "tuft")
    # set_resistivity(cell, "0.3822 kohm_cm", "apical")

    # cell.biophysical_properties.intracellular_properties.species.append(Species(id="ca", concentration_model="cad", ion="ca", initial_concentration="100e-6 mM",
    #                         initial_ext_concentration="2 mM", segment_groups="tuft"))

    pyr_cell_doc.cells.append(cell)
    pynml.write_neuroml2_file(nml2_doc=pyr_cell_doc, nml2_file_name=nml_cell_file, validate=True)
    return nml_cell_file 

create_pyr_cell()

pyNeuroML >>> INFO - Executing: (java -Xmx400M  -jar  "/Users/shayan/opt/anaconda3/envs/neuron/lib/python3.10/site-packages/pyneuroml/lib/jNeuroML-0.12.0-jar-with-dependencies.jar" -validate "pyr.cell.nml" ) in directory: .
pyNeuroML >>> INFO - Command completed. Output: 
  jNeuroML >>   jNeuroML v0.12.0
  jNeuroML >>  Validating: /Users/shayan/Desktop/OSB/BahlEtAl2012_ReducedL5PyrCell/NeuroML2/pyr.cell.nml
  jNeuroML >>  Valid against schema and all tests
  jNeuroML >>  
  jNeuroML >>    Warning, check: 100005 (Segment Group used in the include element of segmentGroup should probably be defined BEFORE it is used in the segmentGroup in which it is included, for optimal portability) failed! ... SegmentGroup: soma_group, includes: soma_0
  jNeuroML >>  
  jNeuroML >>  Validated 1 files: 0 passed, 1 passed with warnings, 
  jNeuroML >>  
  jNeuroML >>  


'pyr.cell.nml'

In [107]:
def create_pyr_network():
    """Create the network

    :returns: name of network nml file
    """
    net_doc = NeuroMLDocument(id="network",
                              notes="Pyramidal cell network")
    net_doc_fn = "pyr_multi_comp_net.nml"
    net_doc.includes.append(IncludeType(href=create_pyr_cell()))
    # Create a population: convenient to create many cells of the same type
    pop = Population(id="pop0", notes="A population for pyramidal cell", component="pyr", size=1)
    # Input
    pulsegen = PulseGenerator(id="pg", notes="Simple pulse generator", delay="100ms", duration="500ms", amplitude="0.4nA")

    exp_input = ExplicitInput(target="pop0[0]", input="pg")

    net = Network(id="single_pyr_cell_network",
                  type="networkWithTemperature",
                  temperature = "37 degC",
                  note="A network with a single population")
    net_doc.pulse_generators.append(pulsegen)
    net.explicit_inputs.append(exp_input)
    net.populations.append(pop)
    net_doc.networks.append(net)

    pynml.write_neuroml2_file(nml2_doc=net_doc, nml2_file_name=net_doc_fn, validate=True)
    return net_doc_fn

In [129]:
if __name__ == "__main__":
    main()

pyNeuroML >>> INFO - Executing: (java -Xmx400M  -jar  "/Users/shayan/opt/anaconda3/envs/neuron/lib/python3.10/site-packages/pyneuroml/lib/jNeuroML-0.12.0-jar-with-dependencies.jar" -validate "pyr.cell.nml" ) in directory: .
pyNeuroML >>> INFO - Command completed. Output: 
  jNeuroML >>   jNeuroML v0.12.0
  jNeuroML >>  Validating: /Users/shayan/Desktop/OSB/BahlEtAl2012_ReducedL5PyrCell/NeuroML2/pyr.cell.nml
  jNeuroML >>  Valid against schema and all tests
  jNeuroML >>  
  jNeuroML >>    Warning, check: 100005 (Segment Group used in the include element of segmentGroup should probably be defined BEFORE it is used in the segmentGroup in which it is included, for optimal portability) failed! ... SegmentGroup: soma_group, includes: soma_0
  jNeuroML >>  
  jNeuroML >>  Validated 1 files: 0 passed, 1 passed with warnings, 
  jNeuroML >>  
  jNeuroML >>  
pyNeuroML >>> INFO - Executing: (java -Xmx400M  -jar  "/Users/shayan/opt/anaconda3/envs/neuron/lib/python3.10/site-packages/pyneuroml/lib

In [130]:
sim_id = "pyr_multi_comp"
plot_data(sim_id)